# Contents
1. [Setup](#Setup)
2. [Data Validation](#Data-Validation)
3. [EDA](#EDA)

# Setup

#### Import Libraries

In [1]:
import requests
import pandas as pd
from datetime import datetime

import tweepy
import yaml

import os
os.chdir('/Users/ashrithreddy/Documents/bitcoin_utils/')

#### Import API keys


In [2]:
if False:
    with open("config/config.yaml", "r") as file:
        config = yaml.safe_load(file)

    cryptocompare_config = config['cryptocompare']

    # Cryptocompare API keys
    api_key = cryptocompare_config['api_key']
    api_key

#### Reading Data

In [3]:
if False:

    import requests
    import pandas as pd
    from datetime import datetime, timedelta

    url = "https://min-api.cryptocompare.com/data/v2/histoday"

    # Starting timestamp (earliest BTC data available)
    start_date = datetime(2013, 4, 28)  # Earliest available date
    end_date = datetime.now()            # Retrieve data up to today

    # Initialize an empty DataFrame to store all data
    all_data = pd.DataFrame()

    # Loop through dates in 365-day chunks
    while start_date < end_date:
        # Set end date for this chunk to be 365 days from start_date or the actual end_date
        chunk_end_date = min(start_date + timedelta(days=364), end_date)
        to_ts = int(chunk_end_date.timestamp())
        
        # Set up the parameters for the API request
        params = {
            'fsym': 'BTC',
            'tsym': 'USD',
            'limit': 365,
            'toTs': to_ts,
            'api_key': api_key
        }

        # Request the data for the chunk
        response = requests.get(url, params=params)
        data = response.json()

        # Check if the response was successful
        if data.get('Response') == 'Success':
            # Access the nested data under 'Data' > 'Data'
            daily_data = data['Data']['Data']
            
            # Extract date and all price-related fields
            dates = [datetime.fromtimestamp(item['time']).date() for item in daily_data]
            open_prices = [item['open'] for item in daily_data]
            high_prices = [item['high'] for item in daily_data]
            low_prices = [item['low'] for item in daily_data]
            close_prices = [item['close'] for item in daily_data]
            volume_from = [item['volumefrom'] for item in daily_data]
            volume_to = [item['volumeto'] for item in daily_data]
            
            # Create DataFrame for this chunk
            chunk_df = pd.DataFrame({
                'Date': pd.to_datetime(dates),
                'Open': open_prices,
                'High': high_prices,
                'Low': low_prices,
                'Close': close_prices,
                'Volume_From': volume_from,
                'Volume_To': volume_to
            })
            
            # Append chunk data to the main DataFrame
            all_data = pd.concat([all_data, chunk_df], ignore_index=True)
            print(f"Data chunk from {start_date.date()} to {chunk_end_date.date()} retrieved successfully.")
        else:
            print("Error retrieving data:", data.get('Message', 'An unknown error occurred'))
        
        # Move start_date to the next day after the current chunk_end_date
        start_date = chunk_end_date + timedelta(days=1)

    # Now all_data contains the full dataset; let's organize it by calendar year
    all_data['Year'] = all_data['Date'].dt.year

    # Save data for each calendar year in separate files
    for year, year_df in all_data.groupby('Year'):
        # Filter data to the specific calendar year and save to CSV
        year_df.to_csv(f'data/BTC_Price_{year}.csv', index=False)
        print(f"Data for {year} saved successfully.")

    # Display the first and last few rows of the complete dataset for verification
    print(all_data.head())
    print(all_data.tail())

[Back to the top](#Contents)

# Data Validation

In [4]:
import pandas as pd
import glob

# Path to the folder containing the CSV files
file_path = 'data/BTC_Price_*.csv'

# Use glob to list all matching files
all_files = glob.glob(file_path)

# Read each CSV file and concatenate them into a single DataFrame
btc_prices = pd.concat([pd.read_csv(file) for file in all_files], ignore_index=True)

# Display the first few rows and basic info for verification
print(btc_prices.head())

         Date     Open     High      Low    Close  Volume_From     Volume_To  \
0  2020-01-01  7189.94  7224.84  6945.83  6965.72     26531.32  1.873940e+08   
1  2020-01-02  6965.72  7407.11  6882.62  7339.70     51975.01  3.766904e+08   
2  2020-01-03  7339.70  7405.75  7278.60  7357.50     22083.57  1.621069e+08   
3  2020-01-04  7357.50  7501.42  7330.07  7359.96     24084.13  1.791477e+08   
4  2020-01-05  7359.96  7799.63  7355.11  7762.69     46443.66  3.522862e+08   

   Year  
0  2020  
1  2020  
2  2020  
3  2020  
4  2020  


- Missing values

In [5]:
btc_prices.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4392 entries, 0 to 4391
Data columns (total 8 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   Date         4392 non-null   object 
 1   Open         4392 non-null   float64
 2   High         4392 non-null   float64
 3   Low          4392 non-null   float64
 4   Close        4392 non-null   float64
 5   Volume_From  4392 non-null   float64
 6   Volume_To    4392 non-null   float64
 7   Year         4392 non-null   int64  
dtypes: float64(6), int64(1), object(1)
memory usage: 274.6+ KB


- Continuity

In [6]:
import pandas as pd

# Ensure the 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# Group by year and calculate the number of days, min date, and max date for each year
yearly_summary = btc_prices.groupby(btc_prices['Date'].dt.year).agg(
    Days_Count=('Date', 'nunique'),
    Min_Date=('Date', 'min'),
    Max_Date=('Date', 'max')
).reset_index().rename(columns={'Date': 'Year'})

# Display the summary
print(yearly_summary)

    Year  Days_Count   Min_Date   Max_Date
0   2013         250 2013-04-26 2013-12-31
1   2014         365 2014-01-01 2014-12-31
2   2015         365 2015-01-01 2015-12-31
3   2016         366 2016-01-01 2016-12-31
4   2017         365 2017-01-01 2017-12-31
5   2018         365 2018-01-01 2018-12-31
6   2019         365 2019-01-01 2019-12-31
7   2020         366 2020-01-01 2020-12-31
8   2021         365 2021-01-01 2021-12-31
9   2022         365 2022-01-01 2022-12-31
10  2023         365 2023-01-01 2023-12-31
11  2024         300 2024-01-01 2024-10-26


[Back to the top](#Contents)

# EDA

#### Line Chart

In [7]:
# import matplotlib.pyplot as plt
# import pandas as pd

# # Ensure the 'Date' column is in datetime format
# btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# # Sort by date to ensure the line chart is chronological
# btc_prices = btc_prices.sort_values('Date')

# # Plotting the line chart
# plt.figure(figsize=(12, 6))
# plt.plot(btc_prices['Date'], btc_prices['Close'], label='Close Price', linewidth=1)

# # Adding labels and title
# plt.xlabel('Date')
# plt.ylabel('BTC Price (USD)')
# plt.title('Bitcoin Closing Prices Over Time')
# plt.legend()
# plt.grid(True)

# # Display the plot
# plt.show()


In [8]:
# import matplotlib.pyplot as plt
# import matplotlib.dates as mdates
# import pandas as pd

# # Ensure the 'Date' column is in datetime format
# btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# # Sort by date to ensure the line chart is chronological
# btc_prices = btc_prices.sort_values('Date')

# # Plotting the line chart with enhanced aesthetics
# plt.figure(figsize=(14, 7))
# plt.plot(btc_prices['Date'], btc_prices['Close'], label='Close Price', color='royalblue', linewidth=1.5)

# # Improving aesthetics
# plt.xlabel('Date', fontsize=14)
# plt.ylabel('BTC Price (USD)', fontsize=14)
# plt.title('Bitcoin Closing Prices Over Time', fontsize=16, fontweight='bold')
# plt.legend(fontsize=12)
# plt.grid(True, linestyle='--', alpha=0.7)

# # Formatting the Y-axis with thousands separators
# plt.ticklabel_format(style='plain', axis='y')
# plt.gca().yaxis.set_major_formatter(plt.FuncFormatter(lambda x, loc: f"{int(x):,}"))

# # Formatting the x-axis to show major ticks yearly and minor ticks monthly
# plt.gca().xaxis.set_major_locator(mdates.YearLocator())
# plt.gca().xaxis.set_minor_locator(mdates.MonthLocator())
# plt.gca().xaxis.set_major_formatter(mdates.DateFormatter('%Y'))

# # Rotate x-axis labels for better readability
# plt.xticks(rotation=45)

# # Display the plot
# plt.show()


In [9]:
# import plotly.graph_objects as go
# import pandas as pd

# # Ensure 'Date' column is in datetime format
# btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# # Create an interactive line chart with Plotly
# fig = go.Figure()

# fig.add_trace(go.Scatter(
#     x=btc_prices['Date'], 
#     y=btc_prices['Close'],
#     mode='lines',
#     name='Close Price',
#     line=dict(color='royalblue', width=1.5),
#     hovertemplate='Date: %{x}<br>Price: $%{y:,.2f}<extra></extra>'
# ))

# # Customize layout
# fig.update_layout(
#     title='Bitcoin Closing Prices Over Time',
#     xaxis_title='Date',
#     yaxis_title='BTC Price (USD)',
#     template='plotly_white',
#     title_x=0.5,
#     font=dict(size=14),
#     hovermode="x unified"
# )

# # Update x-axis for yearly ticks
# fig.update_xaxes(
#     tickformat="%Y",
#     tickangle=45,
#     showgrid=True,
#     gridcolor="LightGrey"
# )

# # Update y-axis to show thousands separator
# fig.update_yaxes(tickprefix="$", showgrid=True, gridcolor="LightGrey")

# # Show the interactive plot
# fig.show()


In [10]:
# import plotly.graph_objects as go
# import pandas as pd

# # Ensure 'Date' column is in datetime format
# btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# # Create an interactive line chart with Plotly
# fig = go.Figure()

# fig.add_trace(go.Scatter(
#     x=btc_prices['Date'], 
#     y=btc_prices['Close'],
#     mode='lines',
#     name='BTC Close Price',  # This label will appear in the legend
#     line=dict(color='royalblue', width=1.5),
#     hovertemplate='Date: %{x}<br>Price: $%{y:,.2f}<extra></extra>'
# ))

# # Customize layout
# fig.update_layout(
#     title='BTC Price',
#     xaxis_title='Date',
#     yaxis_title='BTC Price (USD)',
#     template='plotly_white',
#     title_x=0.5,
#     font=dict(size=14),
#     hovermode="x unified",
#     height=600,  # Make the plot taller
#     legend=dict(
#         title="Legend",
#         orientation="h",
#         yanchor="bottom",
#         y=1.02,
#         xanchor="center",
#         x=0.5
#     )
# )

# # Update x-axis for yearly ticks
# fig.update_xaxes(
#     tickformat="%Y",
#     tickangle=45,
#     showgrid=True,
#     gridcolor="LightGrey"
# )

# # Update y-axis to show thousands separator
# fig.update_yaxes(tickprefix="$", showgrid=True, gridcolor="LightGrey")

# # Show the interactive plot
# fig.show()


In [11]:
import plotly.graph_objects as go
import pandas as pd
from datetime import datetime

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Create an interactive line chart with Plotly
fig = go.Figure()

# Plot the BTC price line
fig.add_trace(go.Scatter(
    x=btc_prices['Date'], 
    y=btc_prices['Close'],
    mode='lines',
    name='BTC Close Price',
    line=dict(color='royalblue', width=1.5),
    hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:,.2f}<extra></extra>',
))

# Add a hidden scatter trace to create the "Election Day" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Election Day',
    line=dict(color='red', width=1, dash='dash')
))

# Add a hidden scatter trace to create the "Halving Event" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Halving Event',
    line=dict(color='green', width=1, dash='dot')
))

# Add vertical lines for Election Days using `add_vline`
election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
for date in election_dates:
    fig.add_vline(
        x=date,
        line=dict(color="red", width=1, dash="dash")
    )

# Add vertical lines for Bitcoin Halving Events using `add_vline`
halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
for date in halving_dates:
    fig.add_vline(
        x=date,
        line=dict(color="green", width=1, dash="dot")
    )

# Customize layout
fig.update_layout(
    title='BTC Price with Key Events',
    xaxis_title='Date',
    yaxis_title='Price',
    template='plotly_white',
    title_x=0.5,
    font=dict(size=14),
    hovermode="x unified",
    height=600,
    legend=dict(
        title="",
        orientation="v",
        yanchor="top",
        y=0.95,
        xanchor="left",
        x=0.05
    )
)

# Update x-axis for more frequent ticks (every 4 months) and rotate labels
fig.update_xaxes(
    dtick="M4",
    tickformat="%Y-%m",
    tickangle=270,
    showgrid=False
)

# Update y-axis to remove gridlines
fig.update_yaxes(showgrid=False)

# Show the interactive plot
fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [12]:
import plotly.graph_objects as go
import pandas as pd
from datetime import datetime

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Define the year range for which to generate plots
start_year = 2013
end_year = 2024

# Loop through each year in the specified range
for year in range(start_year, end_year + 1):
    # Filter data for the current year
    min_date = datetime(year, 1, 1)
    max_date = datetime(year, 12, 31)
    filtered_data = btc_prices[(btc_prices['Date'] >= min_date) & (btc_prices['Date'] <= max_date)]
    
    # Set x-axis range dynamically based on filtered data
    x_axis_range = [filtered_data['Date'].min(), filtered_data['Date'].max()] if not filtered_data.empty else None
    
    # Create a new figure for the current year
    fig = go.Figure()

    # Plot the BTC price line within the filtered date range
    fig.add_trace(go.Scatter(
        x=filtered_data['Date'], 
        y=filtered_data['Close'],
        mode='lines',
        name='BTC Close Price',
        line=dict(color='royalblue', width=1.5),
        hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:,.2f}<extra></extra>',
    ))

    # Add a hidden scatter trace to create the "Election Day" legend entry
    fig.add_trace(go.Scatter(
        x=[None],
        y=[None],
        mode='lines',
        name='Election Day',
        line=dict(color='red', width=1, dash='dash')
    ))

    # Add a hidden scatter trace to create the "Halving Event" legend entry
    fig.add_trace(go.Scatter(
        x=[None],
        y=[None],
        mode='lines',
        name='Halving Event',
        line=dict(color='green', width=1, dash='dot')
    ))

    # Add vertical lines for Election Days in the current year using `add_vline`
    election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
    for date in election_dates:
        if min_date <= date <= max_date:  # Only add if within the filter range
            fig.add_vline(
                x=date,
                line=dict(color="red", width=1, dash="dash")
            )

    # Add vertical lines for Bitcoin Halving Events in the current year using `add_vline`
    halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
    for date in halving_dates:
        if min_date <= date <= max_date:  # Only add if within the filter range
            fig.add_vline(
                x=date,
                line=dict(color="green", width=1, dash="dot")
            )

    # Customize layout
    fig.update_layout(
        title=f'BTC Price with Key Events in {year}',
        xaxis_title='Date',
        yaxis_title='Price',
        template='plotly_white',
        title_x=0.5,
        font=dict(size=14),
        hovermode="x unified",
        height=600,
        legend=dict(
            title="",
            orientation="v",
            yanchor="top",
            y=0.95,
            xanchor="left",
            x=0.05
        )
    )

    # Update x-axis for more frequent ticks and rotate labels
    fig.update_xaxes(
        dtick="M1",           # Set monthly ticks for each year plot
        tickformat="%Y-%m",
        tickangle=270,
        showgrid=False,
        range=x_axis_range  # Dynamically set the x-axis range based on filtered data
    )

    # Update y-axis to remove gridlines
    fig.update_yaxes(showgrid=False)

    # Show the plot for the current year
    fig.show()  # Display in notebook


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



- Log Scale

In [13]:
import plotly.graph_objects as go
import pandas as pd
from datetime import datetime

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Create an interactive line chart with Plotly
fig = go.Figure()

# Plot the BTC price line with a logarithmic y-axis
fig.add_trace(go.Scatter(
    x=btc_prices['Date'], 
    y=btc_prices['Close'],
    mode='lines',
    name='BTC Close Price',
    line=dict(color='royalblue', width=1.5),
    hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:,.2f}<extra></extra>',
))

# Add a hidden scatter trace to create the "Election Day" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Election Day',
    line=dict(color='red', width=1, dash='dash')
))

# Add a hidden scatter trace to create the "Halving Event" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Halving Event',
    line=dict(color='green', width=1, dash='dot')
))

# Add vertical lines for Election Days using `add_vline`
election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
for date in election_dates:
    fig.add_vline(
        x=date,
        line=dict(color="red", width=1, dash="dash")
    )

# Add vertical lines for Bitcoin Halving Events using `add_vline`
halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
for date in halving_dates:
    fig.add_vline(
        x=date,
        line=dict(color="green", width=1, dash="dot")
    )

# Customize layout
fig.update_layout(
    title='BTC Price with Key Events (Logarithmic Scale)',
    xaxis_title='Date',
    yaxis_title='Price (Log Scale)',
    template='plotly_white',
    title_x=0.5,
    font=dict(size=14),
    hovermode="x unified",
    height=600,
    legend=dict(
        title="",
        orientation="v",
        yanchor="top",
        y=0.95,
        xanchor="left",
        x=0.05
    )
)

# Update x-axis for more frequent ticks (every 4 months) and rotate labels
fig.update_xaxes(
    dtick="M4",
    tickformat="%Y-%m",
    tickangle=270,
    showgrid=False
)

# Update y-axis to logarithmic scale with custom tick values for better readability
fig.update_yaxes(
    type="log",
    showgrid=True,
    tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000],  # 2 and 5 progression
    ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k"]
)

# Show the interactive plot
fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [14]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from datetime import datetime
from sklearn.linear_model import LinearRegression

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Log transform the price data for trendline calculation
btc_prices['Log_Close'] = np.log(btc_prices['Close'])

# Prepare data for linear regression
# Convert date to ordinal for regression and reshape
dates_ordinal = btc_prices['Date'].map(datetime.toordinal).values.reshape(-1, 1)
prices_log = btc_prices['Log_Close'].values.reshape(-1, 1)

# Fit a linear regression model on the log-transformed prices
model = LinearRegression().fit(dates_ordinal, prices_log)

# Generate trendline values based on the model
trendline_log = model.predict(dates_ordinal).flatten()
trendline = np.exp(trendline_log)  # Inverse of log to get back to original scale

# Create the plot
fig = go.Figure()

# Plot the BTC price line with a logarithmic y-axis
fig.add_trace(go.Scatter(
    x=btc_prices['Date'], 
    y=btc_prices['Close'],
    mode='lines',
    name='BTC Close Price',
    line=dict(color='royalblue', width=1.5),
    hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:,.2f}<extra></extra>',
))

# Add the trendline
fig.add_trace(go.Scatter(
    x=btc_prices['Date'],
    y=trendline,
    mode='lines',
    name='Trendline',
    line=dict(color='orange', width=2, dash='dash'),
    hovertemplate='Trendline Price: $%{y:,.2f}<extra></extra>',
))

# Add a hidden scatter trace to create the "Election Day" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Election Day',
    line=dict(color='red', width=1, dash='dash')
))

# Add a hidden scatter trace to create the "Halving Event" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Halving Event',
    line=dict(color='green', width=1, dash='dot')
))

# Add vertical lines for Election Days using `add_vline`
election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
for date in election_dates:
    fig.add_vline(
        x=date,
        line=dict(color="red", width=1, dash="dash")
    )

# Add vertical lines for Bitcoin Halving Events using `add_vline`
halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
for date in halving_dates:
    fig.add_vline(
        x=date,
        line=dict(color="green", width=1, dash="dot")
    )

# Customize layout
fig.update_layout(
    title='BTC Price with Key Events and Trendline (Logarithmic Scale)',
    xaxis_title='Date',
    yaxis_title='Price (Log Scale)',
    template='plotly_white',
    title_x=0.5,
    font=dict(size=14),
    hovermode="x unified",
    height=600,
    legend=dict(
        title="",
        orientation="v",
        yanchor="top",
        y=0.95,
        xanchor="left",
        x=0.05
    )
)

# Update x-axis for more frequent ticks (every 4 months) and rotate labels
fig.update_xaxes(
    dtick="M4",
    tickformat="%Y-%m",
    tickangle=270,
    showgrid=False
)

# Update y-axis to logarithmic scale with custom tick values for better readability
fig.update_yaxes(
    type="log",
    showgrid=True,
    tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000],
    ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k"]
)

# Show the interactive plot
fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [15]:
# import plotly.graph_objects as go
# import pandas as pd
# import numpy as np
# from datetime import datetime
# from sklearn.linear_model import LinearRegression

# # Ensure 'Date' column is in datetime format
# btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])

# # Log base 10 transform the price data for trendline calculation
# btc_prices['Log10_Close'] = np.log10(btc_prices['Close'])

# # Prepare data for linear regression
# # Convert date to ordinal for regression and reshape
# dates_ordinal = btc_prices['Date'].map(datetime.toordinal).values.reshape(-1, 1)
# prices_log10 = btc_prices['Log10_Close'].values.reshape(-1, 1)

# # Fit a linear regression model on the log10-transformed prices
# model = LinearRegression().fit(dates_ordinal, prices_log10)

# # Generate trendline values based on the model
# trendline_log10 = model.predict(dates_ordinal).flatten()
# trendline = 10 ** trendline_log10  # Inverse of log10 to get back to original scale

# # Create the plot
# fig = go.Figure()

# # Plot the BTC price line with a logarithmic (base 10) y-axis
# fig.add_trace(go.Scatter(
#     x=btc_prices['Date'], 
#     y=btc_prices['Close'],
#     mode='lines',
#     name='BTC Close Price',
#     line=dict(color='royalblue', width=1.5),
#     hovertemplate='Date: %{x|%Y-%m-%d}<br>Price: $%{y:,.2f}<extra></extra>',
# ))

# # Add the trendline
# fig.add_trace(go.Scatter(
#     x=btc_prices['Date'],
#     y=trendline,
#     mode='lines',
#     name='Trendline',
#     line=dict(color='orange', width=2, dash='dash'),
#     hovertemplate='Trendline Price: $%{y:,.2f}<extra></extra>',
# ))

# # Add a hidden scatter trace to create the "Election Day" legend entry
# fig.add_trace(go.Scatter(
#     x=[None],
#     y=[None],
#     mode='lines',
#     name='Election Day',
#     line=dict(color='red', width=1, dash='dash')
# ))

# # Add a hidden scatter trace to create the "Halving Event" legend entry
# fig.add_trace(go.Scatter(
#     x=[None],
#     y=[None],
#     mode='lines',
#     name='Halving Event',
#     line=dict(color='green', width=1, dash='dot')
# ))

# # Add vertical lines for Election Days using `add_vline`
# election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
# for date in election_dates:
#     fig.add_vline(
#         x=date,
#         line=dict(color="red", width=1, dash="dash")
#     )

# # Add vertical lines for Bitcoin Halving Events using `add_vline`
# halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
# for date in halving_dates:
#     fig.add_vline(
#         x=date,
#         line=dict(color="green", width=1, dash="dot")
#     )

# # Customize layout
# fig.update_layout(
#     title='BTC Price with Key Events and Trendline (Logarithmic Scale, Base 10)',
#     xaxis_title='Date',
#     yaxis_title='Price (Log Scale, Base 10)',
#     template='plotly_white',
#     title_x=0.5,
#     font=dict(size=14),
#     hovermode="x unified",
#     height=600,
#     legend=dict(
#         title="",
#         orientation="v",
#         yanchor="top",
#         y=0.95,
#         xanchor="left",
#         x=0.05
#     )
# )

# # Update x-axis for more frequent ticks (every 4 months) and rotate labels
# fig.update_xaxes(
#     dtick="M4",
#     tickformat="%Y-%m",
#     tickangle=270,
#     showgrid=False
# )

# # Update y-axis to log base 10 scale with custom tick values for better readability
# fig.update_yaxes(
#     type="log",
#     showgrid=True,
#     tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000],
#     ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k"]
# )

# # Show the interactive plot
# fig.show()


In [16]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from datetime import datetime
from sklearn.linear_model import LinearRegression

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Define the price columns to iterate over
price_columns = ['Open', 'High', 'Low', 'Close']

# Loop through each price type and generate a separate plot
for price_col in price_columns:
    # Log transform the price data for trendline calculation
    log_price = np.log(btc_prices[price_col])

    # Prepare data for linear regression
    # Convert date to ordinal for regression and reshape
    dates_ordinal = btc_prices['Date'].map(datetime.toordinal).values.reshape(-1, 1)
    prices_log = log_price.values.reshape(-1, 1)

    # Fit a linear regression model on the log-transformed prices
    model = LinearRegression().fit(dates_ordinal, prices_log)

    # Generate trendline values based on the model
    trendline_log = model.predict(dates_ordinal).flatten()
    trendline = np.exp(trendline_log)  # Inverse of log to get back to original scale

    # Create the plot
    fig = go.Figure()

    # Plot the BTC price line with a logarithmic y-axis
    fig.add_trace(go.Scatter(
        x=btc_prices['Date'], 
        y=btc_prices[price_col],
        mode='lines',
        name=f'BTC {price_col} Price',
        line=dict(color='royalblue', width=1.5),
        hovertemplate=f'Date: %{{x|%Y-%m-%d}}<br>{price_col} Price: $%{{y:,.2f}}<extra></extra>',
    ))

    # Add the trendline
    fig.add_trace(go.Scatter(
        x=btc_prices['Date'],
        y=trendline,
        mode='lines',
        name='Trendline',
        line=dict(color='orange', width=2, dash='dash'),
        hovertemplate='Trendline Price: $%{y:,.2f}<extra></extra>',
    ))

    # Add a hidden scatter trace to create the "Election Day" legend entry
    fig.add_trace(go.Scatter(
        x=[None],
        y=[None],
        mode='lines',
        name='Election Day',
        line=dict(color='red', width=1, dash='dash')
    ))

    # Add a hidden scatter trace to create the "Halving Event" legend entry
    fig.add_trace(go.Scatter(
        x=[None],
        y=[None],
        mode='lines',
        name='Halving Event',
        line=dict(color='green', width=1, dash='dot')
    ))

    # Add vertical lines for Election Days using `add_vline`
    election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5)]
    for date in election_dates:
        fig.add_vline(
            x=date,
            line=dict(color="red", width=1, dash="dash")
        )

    # Add vertical lines for Bitcoin Halving Events using `add_vline`
    halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1)]
    for date in halving_dates:
        fig.add_vline(
            x=date,
            line=dict(color="green", width=1, dash="dot")
        )

    # Customize layout
    fig.update_layout(
        title=f'BTC {price_col} Price with Key Events and Trendline (Logarithmic Scale)',
        xaxis_title='Date',
        yaxis_title='Price (Log Scale)',
        template='plotly_white',
        title_x=0.5,
        font=dict(size=14),
        hovermode="x unified",
        height=600,
        legend=dict(
            title="",
            orientation="v",
            yanchor="top",
            y=0.95,
            xanchor="left",
            x=0.05
        )
    )

    # Update x-axis for more frequent ticks (every 4 months) and rotate labels
    fig.update_xaxes(
        dtick="M4",
        tickformat="%Y-%m",
        tickangle=270,
        showgrid=False
    )

    # Update y-axis to logarithmic scale with custom tick values for better readability
    fig.update_yaxes(
        type="log",
        showgrid=True,
        tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000],
        ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k"]
    )

    # Show the interactive plot
    fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [17]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from sklearn.linear_model import LinearRegression

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Log transform the close price data for trendline calculation
btc_prices['Log_Close'] = np.log(btc_prices['Close'])

# Prepare data for linear regression
# Convert date to ordinal for regression and reshape
dates_ordinal = btc_prices['Date'].map(datetime.toordinal).values.reshape(-1, 1)
prices_log = btc_prices['Log_Close'].values.reshape(-1, 1)

# Fit a linear regression model on the log-transformed close prices
model = LinearRegression().fit(dates_ordinal, prices_log)

# Generate trendline values for the historical data based on the model
trendline_log = model.predict(dates_ordinal).flatten()
trendline = np.exp(trendline_log)  # Inverse of log to get back to original scale

# Extend dates for the next 5 years
last_date = btc_prices['Date'].max()
future_dates = [last_date + timedelta(days=i) for i in range(1, 5 * 365 + 1)]
future_dates_ordinal = np.array([date.toordinal() for date in future_dates]).reshape(-1, 1)

# Predict trendline values for future dates
future_trendline_log = model.predict(future_dates_ordinal).flatten()
future_trendline = np.exp(future_trendline_log)  # Convert log scale back to original scale

# Create the plot
fig = go.Figure()

# Plot the BTC close price line with a logarithmic y-axis
fig.add_trace(go.Scatter(
    x=btc_prices['Date'], 
    y=btc_prices['Close'],
    mode='lines',
    name='BTC Close Price',
    line=dict(color='royalblue', width=1.5),
    hovertemplate='Date: %{x|%Y-%m-%d}<br>Close Price: $%{y:,.2f}<extra></extra>',
))

# Add the historical trendline
fig.add_trace(go.Scatter(
    x=btc_prices['Date'],
    y=trendline,
    mode='lines',
    name='Trendline',
    line=dict(color='orange', width=2, dash='dash'),
    hovertemplate='Trendline Price: $%{y:,.2f}<extra></extra>',
))

# Add the extrapolated trendline for future dates
fig.add_trace(go.Scatter(
    x=future_dates,
    y=future_trendline,
    mode='lines',
    name='Extrapolated Trendline',
    line=dict(color='orange', width=2, dash='dot'),
    hovertemplate='Extrapolated Price: $%{y:,.2f}<extra></extra>',
))

# Add a hidden scatter trace to create the "Election Day" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Election Day',
    line=dict(color='red', width=1, dash='dash')
))

# Add a hidden scatter trace to create the "Halving Event" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Halving Event',
    line=dict(color='green', width=1, dash='dot')
))

# Add vertical lines for Election Days using `add_vline`
election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5), datetime(2028, 11, 7), datetime(2032, 11, 2)]
for date in election_dates:
    fig.add_vline(
        x=date,
        line=dict(color="red", width=1, dash="dash")
    )

# Add vertical lines for Bitcoin Halving Events using `add_vline`
halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1), datetime(2028, 3, 1)]
for date in halving_dates:
    fig.add_vline(
        x=date,
        line=dict(color="green", width=1, dash="dot")
    )

# Customize layout
fig.update_layout(
    title='BTC Close Price with Key Events and Extrapolated Trendline (Logarithmic Scale)',
    xaxis_title='Date',
    yaxis_title='Price (Log Scale)',
    template='plotly_white',
    title_x=0.5,
    font=dict(size=14),
    hovermode="x unified",
    height=600,
    legend=dict(
        title="",
        orientation="v",
        yanchor="top",
        y=0.95,
        xanchor="left",
        x=0.05
    )
)

# Update x-axis for more frequent ticks (every 4 months) and rotate labels
fig.update_xaxes(
    dtick="M6",
    tickformat="%Y-%m",
    tickangle=270,
    showgrid=False
)

# Update y-axis to logarithmic scale with expanded tick values for millions
fig.update_yaxes(
    type="log",
    showgrid=True,
    tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000, 200000, 500000, 1000000, 2000000, 5000000, 10000000],
    ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k", "$200k", "$500k", "$1M", "$2M", "$5M", "$10M"]
)

# Show the interactive plot
fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [18]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
from sklearn.linear_model import LinearRegression

# Ensure 'Date' column is in datetime format
btc_prices['Date'] = pd.to_datetime(btc_prices['Date'])
btc_prices = btc_prices.sort_values(by='Date')

# Log transform the close price data for trendline calculation
btc_prices['Log_Close'] = np.log(btc_prices['Close'])

# Prepare data for linear regression
# Convert date to ordinal for regression and reshape
dates_ordinal = btc_prices['Date'].map(datetime.toordinal).values.reshape(-1, 1)
prices_log = btc_prices['Log_Close'].values.reshape(-1, 1)

# Fit a linear regression model on the log-transformed close prices
model = LinearRegression().fit(dates_ordinal, prices_log)

# Generate trendline values for the historical data based on the model
trendline_log = model.predict(dates_ordinal).flatten()
trendline = np.exp(trendline_log)  # Inverse of log to get back to original scale

# Extend dates for the next 5 years
last_date = btc_prices['Date'].max()
future_dates = [last_date + timedelta(days=i) for i in range(1, 5 * 365 + 1)]
future_dates_ordinal = np.array([date.toordinal() for date in future_dates]).reshape(-1, 1)

# Predict trendline values for future dates
future_trendline_log = model.predict(future_dates_ordinal).flatten()
future_trendline = np.exp(future_trendline_log)  # Convert log scale back to original scale

# Create the plot
fig = go.Figure()

# Plot the BTC close price line with a logarithmic y-axis
fig.add_trace(go.Scatter(
    x=btc_prices['Date'], 
    y=btc_prices['Close'],
    mode='lines',
    name='BTC Close Price',
    line=dict(color='royalblue', width=1.5),
    hovertemplate='Date: %{x|%Y-%m-%d}<br>Close Price: $%{y:,.2f}<extra></extra>',
))

# Add the historical trendline
fig.add_trace(go.Scatter(
    x=btc_prices['Date'],
    y=trendline,
    mode='lines',
    name='Trendline',
    line=dict(color='orange', width=2, dash='dash'),
    hovertemplate='Trendline Price: $%{y:,.2f}<extra></extra>',
))

# Add the extrapolated trendline for future dates
fig.add_trace(go.Scatter(
    x=future_dates,
    y=future_trendline,
    mode='lines',
    name='Extrapolated Trendline',
    line=dict(color='orange', width=2, dash='dot'),
    hovertemplate='Extrapolated Price: $%{y:,.2f}<extra></extra>',
))

# Add a hidden scatter trace to create the "Election Day" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Election Day',
    line=dict(color='red', width=1, dash='dash')
))

# Add a hidden scatter trace to create the "Halving Event" legend entry
fig.add_trace(go.Scatter(
    x=[None],
    y=[None],
    mode='lines',
    name='Halving Event',
    line=dict(color='green', width=1, dash='dot')
))

# Add vertical lines for Election Days using `add_vline`
election_dates = [datetime(2016, 11, 8), datetime(2020, 11, 3), datetime(2024, 11, 5), datetime(2028, 11, 7), datetime(2032, 11, 2)]
for date in election_dates:
    fig.add_vline(
        x=date,
        line=dict(color="red", width=1, dash="dash")
    )

# Add vertical lines for Bitcoin Halving Events using `add_vline`
halving_dates = [datetime(2012, 11, 28), datetime(2016, 7, 9), datetime(2020, 5, 11), datetime(2024, 4, 1), datetime(2028, 3, 1)]
for date in halving_dates:
    fig.add_vline(
        x=date,
        line=dict(color="green", width=1, dash="dot")
    )

# Add small red tick marks at each January date to subtly mark the start of each year
january_dates = btc_prices[btc_prices['Date'].dt.month == 1]['Date'].dt.to_pydatetime().tolist()
for date in january_dates:
    fig.add_shape(
        type="line",
        x0=date, x1=date,
        y0=0, y1=0.05,  # Tick mark height
        xref="x", yref="paper",
        line=dict(color="red", width=1),
    )

# Customize layout
fig.update_layout(
    title='BTC Close Price with Key Events and Extrapolated Trendline (Logarithmic Scale)',
    xaxis_title='Date',
    yaxis_title='Price (Log Scale)',
    template='plotly_white',
    title_x=0.5,
    font=dict(size=14),
    hovermode="x unified",
    height=600,
    legend=dict(
        title="",
        orientation="v",
        yanchor="top",
        y=0.95,
        xanchor="left",
        x=0.05
    )
)

# Update x-axis for more frequent ticks (every 6 months) and rotate labels
fig.update_xaxes(
    dtick="M6",
    tickformat="%Y-%m",
    tickangle=270,
    showgrid=False
)

# Update y-axis to logarithmic scale with expanded tick values for millions
fig.update_yaxes(
    type="log",
    showgrid=True,
    tickvals=[10, 20, 50, 100, 200, 500, 1000, 2000, 5000, 10000, 20000, 50000, 100000, 200000, 500000, 1000000, 2000000, 5000000, 10000000],
    ticktext=["$10", "$20", "$50", "$100", "$200", "$500", "$1k", "$2k", "$5k", "$10k", "$20k", "$50k", "$100k", "$200k", "$500k", "$1M", "$2M", "$5M", "$10M"]
)

# Show the interactive plot
fig.show()


/opt/anaconda3/lib/python3.11/site-packages/_plotly_utils/basevalidators.py:106: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

/var/folders/xj/p0b94bqj0t31lwp_ckhcpwz00000gn/T/ipykernel_7048/1295717453.py:103: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [19]:
# Dates for prediction, covering all dates in the extrapolated future range (5 years)
prediction_dates = pd.date_range(start=last_date + timedelta(days=1), periods=5 * 365)

# Convert these dates to ordinal format
prediction_dates_ordinal = np.array([date.toordinal() for date in prediction_dates]).reshape(-1, 1)

# Predict log-transformed BTC prices for each date in the prediction range
predicted_log_prices = model.predict(prediction_dates_ordinal).flatten()

# Convert log prices to actual BTC prices
predicted_prices = np.exp(predicted_log_prices)

# Create a DataFrame with the dates and corresponding predicted BTC prices
predicted_df = pd.DataFrame({
    'Date': prediction_dates,
    'Predicted_Price': predicted_prices
})

# Display the first few rows of the predictions
pd.options.display.float_format = '{:,.0f}'.format
pd.set_option('display.max_rows', None)  # Show all rows
pd.set_option('display.max_columns', None)  # Show all columns, if there are many

predicted_df.iloc[::10]

# print(predicted_df.head())
# print(predicted_df.tail())
# Reset the float format if you only want this formatting temporarily
# pd.reset_option('display.float_format')

Date  Predicted_Price
0    2024-10-27          106,460
10   2024-11-06          108,084
20   2024-11-16          109,732
30   2024-11-26          111,406
40   2024-12-06          113,105
50   2024-12-16          114,830
60   2024-12-26          116,581
70   2025-01-05          118,359
80   2025-01-15          120,165
90   2025-01-25          121,997
100  2025-02-04          123,858
110  2025-02-14          125,747
120  2025-02-24          127,665
130  2025-03-06          129,612
140  2025-03-16          131,589
150  2025-03-26          133,595
160  2025-04-05          135,633
170  2025-04-15          137,702
180  2025-04-25          139,802
190  2025-05-05          141,934
200  2025-05-15          144,099
210  2025-05-25          146,296
220  2025-06-04          148,528
230  2025-06-14          150,793
240  2025-06-24          153,093
250  2025-07-04          155,428
260  2025-07-14          157,798
270  2025-07-24          160,205
280  2025-08-03          162,648
290  2025-08-13          165,129
300  2025-08-23          167,647
310  2025-09-02          170,204
320  2025-09-12          172,800
330  2025-09-22          175,435
340  2025-10-02          178,111
350  2025-10-12          180,827
360  2025-10-22          183,585
370  2025-11-01          186,385
380  2025-11-11          189,228
390  2025-11-21          192,114
400  2025-12-01          195,044
410  2025-12-11          198,019
420  2025-12-21          201,039
430  2025-12-31          204,105
440  2026-01-10          207,218
450  2026-01-20          210,378
460  2026-01-30          213,587
470  2026-02-09          216,844
480  2026-02-19          220,151
490  2026-03-01          223,509
500  2026-03-11          226,918
510  2026-03-21          230,379
520  2026-03-31          233,892
530  2026-04-10          237,459
540  2026-04-20          241,081
550  2026-04-30          244,758
560  2026-05-10          248,491
570  2026-05-20          252,280
580  2026-05-30          256,128
590  2026-06-09          260,034
600  2026-06-19          264,000
610  2026-06-29          268,027
620  2026-07-09          272,115
630  2026-07-19          276,265
640  2026-07-29          280,478
650  2026-08-08          284,756
660  2026-08-18          289,099
670  2026-08-28          293,508
680  2026-09-07          297,984
690  2026-09-17          302,529
700  2026-09-27          307,143
710  2026-10-07          311,827
720  2026-10-17          316,583
730  2026-10-27          321,412
740  2026-11-06          326,314
750  2026-11-16          331,290
760  2026-11-26          336,343
770  2026-12-06          341,473
780  2026-12-16          346,681
790  2026-12-26          351,968
800  2027-01-05          357,336
810  2027-01-15          362,786
820  2027-01-25          368,319
830  2027-02-04          373,936
840  2027-02-14          379,639
850  2027-02-24          385,429
860  2027-03-06          391,308
870  2027-03-16          397,276
880  2027-03-26          403,335
890  2027-04-05          409,486
900  2027-04-15          415,732
910  2027-04-25          422,072
920  2027-05-05          428,509
930  2027-05-15          435,045
940  2027-05-25          441,680
950  2027-06-04          448,416
960  2027-06-14          455,255
970  2027-06-24          462,198
980  2027-07-04          469,247
990  2027-07-14          476,404
1000 2027-07-24          483,670
1010 2027-08-03          491,047
1020 2027-08-13          498,536
1030 2027-08-23          506,139
1040 2027-09-02          513,859
1050 2027-09-12          521,696
1060 2027-09-22          529,652
1070 2027-10-02          537,730
1080 2027-10-12          545,931
1090 2027-10-22          554,258
1100 2027-11-01          562,711
1110 2027-11-11          571,293
1120 2027-11-21          580,006
1130 2027-12-01          588,852
1140 2027-12-11          597,833
1150 2027-12-21          606,951
1160 2027-12-31          616,208
1170 2028-01-10          625,606
1180 2028-01-20          635,147
1190 2028-01-30          644,834
1200 2028-02-09   

#### [Back to the top](#Contents)

# Junk

In [20]:
# data

In [21]:
# data

In [22]:
# import requests
# import pandas as pd
# from datetime import datetime

# # Define URL and parameters
# url = "https://api.coingecko.com/api/v3/coins/bitcoin/market_chart"
# params = {
#     'vs_currency': 'usd',
#     'days': '365',  # Past 365 days limit for free-tier users
#     'interval': 'daily'
# }

# # Send request
# response = requests.get(url, params=params)
# data = response.json()

# # Check if response contains an error
# if 'prices' in data:
#     dates = [datetime.fromtimestamp(item[0] / 1000).date() for item in data['prices']]
#     prices = [item[1] for item in data['prices']]

#     # Create DataFrame
#     df = pd.DataFrame({'Date': dates, 'Price': prices})
#     print(df.head())
# else:
#     print("Error:", data.get('error', {}).get('error_message', 'An unknown error occurred'))


In [23]:
# df

In [24]:
# import requests

# # Coinbase API endpoint for a specific spot price
# url = "https://api.coinbase.com/v2/prices/BTC-USD/spot"

# response = requests.get(url)
# data = response.json()

# print("Current BTC Price (USD):", data['data']['amount'])


In [25]:
# import requests
# import pandas as pd
# from datetime import datetime

# url = "https://min-api.cryptocompare.com/data/v2/histoday"

# # Define the range of years to retrieve
# start_year = 2015
# end_year = 2024

# # Initialize an empty DataFrame to store all data
# all_data = pd.DataFrame()

# for year in range(start_year, end_year + 1):
#     # Set the timestamp for the end of the current year
#     end_of_year = datetime(year, 12, 31)
#     to_ts = int(end_of_year.timestamp())
    
#     # Set up the parameters for each year's data
#     params = {
#         'fsym': 'BTC',
#         'tsym': 'USD',
#         'limit': 365,  # Maximum of 365 days to capture full year data
#         'toTs': to_ts,
#         'api_key': api_key
#     }

#     # Request the data for the specific year
#     response = requests.get(url, params=params)
#     data = response.json()

#     # Check if the response was successful
#     if data.get('Response') == 'Success':
#         # Access the nested data under 'Data' > 'Data'
#         daily_data = data['Data']['Data']
        
#         # Extract date and all price-related fields
#         dates = [datetime.fromtimestamp(item['time']).date() for item in daily_data]
#         open_prices = [item['open'] for item in daily_data]
#         high_prices = [item['high'] for item in daily_data]
#         low_prices = [item['low'] for item in daily_data]
#         close_prices = [item['close'] for item in daily_data]
#         volume_from = [item['volumefrom'] for item in daily_data]
#         volume_to = [item['volumeto'] for item in daily_data]
        
#         # Create DataFrame for the current year
#         year_df = pd.DataFrame({
#             'Date': dates,
#             'Open': open_prices,
#             'High': high_prices,
#             'Low': low_prices,
#             'Close': close_prices,
#             'Volume_From': volume_from,
#             'Volume_To': volume_to
#         })
#         year_df.to_csv(f'data/BTC_Price_{year}.csv', index=False)
        
#         # Append the year's data to the main DataFrame
#         all_data = pd.concat([all_data, year_df], ignore_index=True)
#         print(f"Data for {year} retrieved successfully.")
#     else:
#         print(f"Error retrieving data for {year}:", data.get('Message', 'An unknown error occurred'))

# # Display the first and last few rows of the complete dataset
# print(all_data.head())
# print(all_data.tail())

In [26]:
# import requests
# import pandas as pd
# from datetime import datetime

# url = "https://min-api.cryptocompare.com/data/v2/histoday"

# # Define the range of years to retrieve
# start_year = 2015
# end_year = 2024

# # Initialize an empty DataFrame to store all data
# all_data = pd.DataFrame()

# for year in range(start_year, end_year + 1):
#     # Set the timestamp for the end of the current year
#     end_of_year = datetime(year, 12, 31)
#     to_ts = int(end_of_year.timestamp())
    
#     # Set up the parameters for each year's data
#     params = {
#         'fsym': 'BTC',
#         'tsym': 'USD',
#         'limit': 366,  # Set to 366 to capture up to December 31
#         'toTs': to_ts,
#         'api_key': api_key
#     }

#     # Request the data for the specific year
#     response = requests.get(url, params=params)
#     data = response.json()

#     # Check if the response was successful
#     if data.get('Response') == 'Success':
#         # Access the nested data under 'Data' > 'Data'
#         daily_data = data['Data']['Data']
        
#         # Extract date and all price-related fields
#         dates = [datetime.fromtimestamp(item['time']).date() for item in daily_data]
#         open_prices = [item['open'] for item in daily_data]
#         high_prices = [item['high'] for item in daily_data]
#         low_prices = [item['low'] for item in daily_data]
#         close_prices = [item['close'] for item in daily_data]
#         volume_from = [item['volumefrom'] for item in daily_data]
#         volume_to = [item['volumeto'] for item in daily_data]
        
#         # Create DataFrame for the current year
#         year_df = pd.DataFrame({
#             'Date': pd.to_datetime(dates),  # Convert dates to pd.Timestamp format
#             'Open': open_prices,
#             'High': high_prices,
#             'Low': low_prices,
#             'Close': close_prices,
#             'Volume_From': volume_from,
#             'Volume_To': volume_to
#         })
        
#         # Filter the DataFrame to only include rows from the target year
#         year_df = year_df[(year_df['Date'] >= f'{year}-01-01') & 
#                           (year_df['Date'] <= f'{year}-12-31')]
        
#         # Save the filtered data to a CSV file
#         year_df.to_csv(f'data/BTC_Price_{year}.csv', index=False)
        
#         # Append the year's filtered data to the main DataFrame
#         all_data = pd.concat([all_data, year_df], ignore_index=True)
#         print(f"Data for {year} retrieved and filtered successfully.")
#     else:
#         print(f"Error retrieving data for {year}:", data.get('Message', 'An unknown error occurred'))

# # Display the first and last few rows of the complete dataset
# print(all_data.head())
# print(all_data.tail())


In [27]:
# import pandas as pd

# # Ensure 'Date' column is in datetime format
# all_data['Date'] = pd.to_datetime(all_data['Date'])

# # Extract the year from the 'Date' column
# all_data['Year'] = all_data['Date'].dt.year

# # Group by year and calculate min date, max date, and count of unique dates
# yearly_summary = all_data.groupby('Year').agg(
#     Min_Date=('Date', 'min'),
#     Max_Date=('Date', 'max'),
#     Unique_Dates_Count=('Date', 'nunique')
# ).reset_index()

# print(yearly_summary)


[Back to the top](#Contents)